In [1]:
import numpy as np
import gurobipy as grb
import csv
import time
import statsmodels.api as sm
from joblib import Parallel,delayed

def five_variate(n,SNR,rho):
    beta1 = np.array([1,1,1,0,1])
    beta2 = np.array([-1,-1,-1,0,-1])
    p = len(beta1)
    Sigma = np.zeros((p,p));
    for i in range(p):
        for j in range(p):
            Sigma[i,j] = rho**(abs(i-j))
    X = np.random.multivariate_normal(mean =np.zeros(p), cov = Sigma, size = n)
    noise1 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta1)/SNR), size = int(n/2)) 
    noise2 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta2)/SNR), size = int(n/2)) 
    Y1 = X[:int(n/2)]@beta1 + noise1
    Y2 = X[int(n/2):]@beta2 + noise2
    Y = np.r_[Y1,Y2]
    lam = 0.1*n
    ols = sm.OLS(Y, X)
    ols_result = ols.fit()
    bigM = 10*float(1.96*(sum(ols_result.bse)))#1000

    M = grb.Model()
    M.Params.TimeLimit = 400
    beta = M.addMVar((int(n),5), lb = -grb.GRB.INFINITY)
    z = M.addMVar(len(Y) - 1, vtype = grb.GRB.BINARY)
    sum_of_sq = sum((Y[t] - sum(X[t,j]*beta[t,j] for j in range(5)))* (Y[t] - sum(X[t,j]*beta[t,j] for j in range(5))) for t in range(len(Y)))
    for t in range(len(Y)-1):
        for j in range(5):
            M.addConstr(beta[t+1,j] - beta[t,j] <= bigM*z[t])
            M.addConstr(beta[t+1,j] - beta[t,j] >= -bigM*z[t])
    #optional constratins to add more cuts
    M.addConstr(sum(z) <= 5)
    for t in range(1, len(Y) - 2):
        M.addConstr(z[t-1] + z[t] + z[t+1] <= 1)
    # l2-reg
    phi = 0.0001*n
    l2_penalty =  phi*sum(sum(beta[t,j]*beta[t,j] for j in range(5)) for t in range(len(Y)))
    M.setObjective(sum_of_sq+ lam*sum(z) + l2_penalty)
    M.optimize()
    beta_hat = [beta[t].x for t in range(len(Y))]
    z_hat = [z[t].x for t in range(len(Y)-1)]
    opt_gap = M.MIPGap
    return z_hat, opt_gap,beta_hat

SNR_list = np.array([6, 3.52, 2.07, 1.22, 0.71])
rho_list = np.array([0, 0.3, 0.7])
n_list = np.array([1000])

header = ['Repitition','Time','rho', 'SNR', 'n', 'Optimality Gap', 'Change Points']#, 'beta_hat', 'nonzero count']
f = open('simulation_five_variate_l2_reg.csv', 'w')
writer = csv.writer(f)
writer.writerow(header)
f.close()

def to_repeat(rep):
    for n in n_list:
        for SNR in SNR_list:
            for rho in rho_list:
                tik = time.time()
                z_hat, opt_gap, beta_hat = five_variate(n,SNR,rho)
                tok = time.time()
                duration = tok - tik
                cps = [idx for idx,item in enumerate(z_hat) if item == 1 ]
                # Write result
                resultrow = [rep,duration,rho,SNR, n, opt_gap, cps]
                f = open('simulation_five_variate_l2_reg.csv', 'a')
                writer = csv.writer(f)
                writer.writerow(resultrow)
                f.close()
                
Parallel(n_jobs = 8)(delayed(to_repeat)(rep) for rep in range(50)) #Tomo's machine has 8 cores.

Set parameter Username
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter Username
Set parameter TimeLimit to value 400
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter TimeLimit to value 400
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter


Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    8607    3.1560352e+03   0.000000e+00   2.152691e+03      5s
   16494    2.6670598e+03   0.000000e+00   1.137835e+03     10s
   12821    3.0038045e+03   0.000000e+00   1.910206e+03     10s
   13241    3.0600343e+03   0.000000e+00   1.544979e+03     10s
   12179    3.2363005e+03   0.000000e+00   1.818438e+03     10s
   12359    3.1805860e+03   0.000000e+00   1.721951e+03     10s
   12725    3.0849683e+03   0.000000e+00   1.648999e+03     10s
   12517    3.1303685e+03   0.000000e+00   1.656043e+03     10s
   13808    2.7811378e+03   0.000000e+00   1.377328e+03     10s
   21161    2.4767765e+03   0.000000e+00   6.663004e+02     15s
   17900    2.6925772e+03   0.000000e+00   9.740990e+02     15s
   18287    2.7792535e+03   0.000000e+00   9.389475e+02     15s
   15419    3.0135493e+03   0.000000e+00   1.372558e+03     15s
   15761    2.9620715e+03   0.000000e+00   1.296746e+03     15s
   15803    2.8896

    27    32 2529.36351    8  309 4727.37683 2529.36351  46.5%  30.6   70s
H   29    32                    3456.7926706 2529.48711  26.8%  29.2   70s
    27    32 2451.98587    8  301 4584.50540 2450.80037  46.5%  26.2   72s
H   28    32                    2754.4378362 2450.80037  11.0%  25.3   72s
    27    32 2573.54068    8  306 4759.17212 2568.19114  46.0%  33.2   72s
H   28    32                    2843.1192059 2568.19114  9.67%  32.0   72s
    27    32 2445.04654    8  320 4490.53250 2441.35839  45.6%  28.0   73s
H   28    32                    4149.6585535 2441.35839  41.2%  27.0   73s
H   29    32                    3579.9970264 2441.35839  31.8%  27.8   73s
    27    32 2305.95046    8  285 4315.33068 2303.30254  46.6%  27.9   72s
H   28    32                    2553.3584313 2303.30254  9.79%  26.9   72s
    40    45 2453.74736   11  302 2754.43784 2450.80037  11.0%  24.7   75s
    84    92 2371.04356   23  301 2663.09139 2356.74199  11.5%  21.6   75s
    35    40 2447.54181  

H  229   240                    3353.5731173 2532.20201  24.5%  19.5  133s
   171   181 2603.12378   72  317 3317.91308 2542.75945  23.4%  25.5  133s
   153   148 2589.10993   37  309 2843.11921 2568.19114  9.67%  63.8  134s
   362   365 2544.58785  100  299 2754.43783 2450.80037  11.0%  19.7  135s
   192   167 2546.42249   40  300 2786.73205 2520.29236  9.56%  46.6  135s
   239   280 2564.06776   64  294 3353.57312 2532.20201  24.5%  19.5  136s
   571   541 2610.47692  142  281 2660.72139 2356.74199  11.4%  17.8  137s
   167   160 2590.58379   40  311 2843.11921 2568.19114  9.67%  59.6  137s
   148   144 2319.90110   34  293 2553.35843 2303.30254  9.79%  66.8  137s
   180   195 2605.50899   77  315 3317.91308 2542.75945  23.4%  25.2  138s
   625   582 2647.20116  151  279 2660.72139 2356.74199  11.4%  17.8  140s
   230   199 2548.99482   45  297 2786.73205 2520.29236  9.56%  43.4  140s
   413   458 2561.91007  111  296 2754.43783 2450.80037  11.0%  19.9  142s
   321   368 2570.25695  

   697   753 2644.30606  180  311 3072.04100 2542.75945  17.2%  19.6  207s
  1121  1206 2727.24205  285  269 3310.53960 2532.20201  23.5%  18.0  208s
   752   817 2646.46382  192  314 3072.04100 2542.75945  17.2%  19.4  211s
   792   869 2656.22914  192  296 3559.14390 2441.35839  31.4%  19.1  211s
  1690  1556 2697.14393  426  214 2754.43783 2450.80037  11.0%  18.1  213s
   953   940 2665.36256  241  292 2843.11921 2568.19114  9.67%  23.9  213s
   860   827 2475.67012  221  248 2553.35843 2303.30254  9.79%  27.6  212s
  1205  1280 2732.44371  305  266 3310.53960 2532.20201  23.5%  17.8  214s
  1258  1188 2752.55552  295  248 2786.73205 2520.29236  9.56%  22.8  214s
  1320  1124 2641.00096  121  294 2660.72139 2362.26248  11.2%  17.8  215s
   816   870 2652.73968  209  301 3072.04100 2542.75945  17.2%  19.3  215s
   868   942 2662.83958  214  288 3559.14390 2441.35839  31.4%  19.0  216s
   932   875 2479.43751  241  239 2553.35843 2303.30254  9.79%  26.7  216s
   959   995 2665.67540  

...

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[x86])

CPU model: Intel(R) Core(TM) i5-8257U CPU @ 1.40GHz
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 10988 rows, 5999 columns and 33960 nonzeros
Model fingerprint: 0x3c507ccf
Model has 15000 quadratic objective terms
Variable types: 5000 continuous, 999 integer (999 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+01]
  Objective range  [3e-04, 1e+02]
  QObjective range [5e-05, 4e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 5e+00]
Found heuristic solution: objective 12456.461376
Presolve time: 0.04s
Presolved: 10988 rows, 5999 columns, 33960 nonzeros
Presolved model has 15000 quadratic objective terms
Variable types: 5000 continuous, 999 integer (999 binary)
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[x86])

CPU model: Intel(R) Core(TM) i5-8257U CPU @ 1.40GHz
Thread count: 4 physical cores, 8 logical processors, using up to 8 thr

  4213  4185 8683.59151  141  370 10764.8703 8001.81506  25.7%  27.8  208s
  4147  4122 7531.04905   14  338 9434.75340 7302.35011  22.6%  30.7  210s
  4216  4190 8001.81506   12  372 10764.8703 8001.81506  25.7%  33.0  210s
  4234  4204 8274.08787   15  332 10764.8703 8001.81506  25.7%  33.6  215s
  4163  4133 7557.35245   16  344 9434.75340 7302.35011  22.6%  31.3  219s
  4171  4138 7548.21198   17  340 9434.75340 7302.35011  22.6%  31.6  220s
  4242  4210 8274.16113   16  333 10764.8703 8001.81506  25.7%  33.9  224s
H 4243  3999                    10549.147599 8001.81506  24.1%  33.9  224s
  4193  4156 7306.56076   20  385 9434.75340 7306.56076  22.6%  32.3  225s
  4246  4002 8001.81506   17  377 10549.1476 8001.81506  24.1%  34.2  225s
  4218  4170 7585.90567   22  339 9434.75340 7311.09569  22.5%  33.1  230s
  4267  4017 8283.34857   19  332 10549.1476 8001.81506  24.1%  34.8  230s
  4237  4186 7347.52815   25  383 9434.75340 7347.52815  22.1%  33.6  235s
  4291  4034 8301.45908  

   25755    1.0915017e+04   0.000000e+00   0.000000e+00     12s

Root relaxation: objective 1.091502e+04, 25755 iterations, 12.10 seconds (14.69 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 10915.0166    0  451 22091.1609 10915.0166  50.6%     -   12s
   25048    1.0969151e+04   0.000000e+00   0.000000e+00     12s

Root relaxation: objective 1.096915e+04, 25048 iterations, 12.13 seconds (14.61 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 10969.1514    0  463 23390.8328 10969.1514  53.1%     -   12s
H    0     0                    23253.885273 10969.1514  52.8%     -   13s
     0     0 10921.7991    0  451 22091.1609 10921.7991  50.6%     -   14s
     0     0 11006.8576    0  463 23253.8853 11006.8576  52.7%     -   14s
H    0 

  4613  4338 11771.1665   24  415 16446.2808 11248.6938  31.6%  39.9  236s
  4406  4140 11141.9860   26  459 15956.2613 11138.8758  30.2%  38.2  236s
H 4407  3935                    15896.994146 11138.8758  29.9%  38.2  236s
H 4408  3742                    15877.447852 11138.8758  29.8%  38.2  236s
  4426  3760 11162.1199   28  461 15877.4479 11162.1199  29.7%  38.8  241s
  4635  4356 11262.4555   27  478 16446.2808 11262.4555  31.5%  40.6  241s
  4444  3772 11176.5169   30  461 15877.4479 11176.5169  29.6%  39.4  245s
  4652  4368 11294.3938   29  478 16446.2808 11294.3938  31.3%  41.2  245s
  4473  3793 11204.5616   33  464 15877.4479 11204.5616  29.4%  40.3  251s
  4679  4386 11332.7972   32  479 16446.2808 11332.7972  31.1%  42.0  251s
  4696  4400 11368.9560   34  485 16446.2808 11368.9560  30.9%  42.6  255s
  4495  3808 11698.8489   35  410 15877.4479 11234.3377  29.2%  40.9  255s
  4720  4415 11930.3150   36  434 16446.2808 11401.7946  30.7%  43.2  260s
  4527  3830 11733.3142  

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]